> 이 문서의 폰트크기는 브라우저 인쇄시 인쇄 배율 80%로 최적화 되어 있음

## (주제) DCGAN 기반  MNIST 분류 시스템

> 1. 시스템 파라미터 설정    
> 2. 시스템 초기화    
> 3. 데이터셋 및 데이터 로더 제작    
> 4. Generator와 Discrimination network 생성    
> 5. 손실함수와 옵티마이저 설정
> 6. 훈련(Training)   
     

In [13]:
# multi line 출력을 위한 셀 -- 필요시 주석해제 후 이 셀을 실행시키기 바람
#from IPython.core.interactiveshell import InteractiveShell
#InteractiveShell.ast_node_interactivity = "all"

In [14]:
import os
import sys

import numpy as np

import torch
import torch.nn as nn
import torch.nn.parallel
import torch.backends.cudnn as cudnn
import torch.optim as optim

import torch.utils.data
import torchvision.datasets as datasets
import torchvision.transforms as transforms
import torchvision.utils as vutils

# 시스템 상수

In [15]:
################# CUDA #################################
USE_GPU_ = True   # Change to False for CPU training even if GPU is available

if USE_GPU_ and torch.cuda.is_available(): 
    DEVICE = 'cuda:0'
    print("CUDA version: {}\n".format(torch.version.cuda))
else:
    DEVICE = 'cpu'

print(DEVICE)

################# 폴더 곤련 ###########################
OUT_PATH = './output'   
LOG_FILE = os.path.join(OUT_PATH, 'log.txt')

################# 학습데이터 및 데이터셋/로더 ##########
DATA_PATH = './'  # 학습데이터 폴더 위치
# DATA_PATH = '/media/john/FastData/CelebA'
# DATA_PATH = '/media/john/FastData/lsun'

X_DIM = 64        # 이미지 H, W의 픽셀 크기
IMAGE_CHANNEL = 1
# IMAGE_CHANNEL = 3

WORKERS = 2     # 데이터로더에 사용할 worker 개수

################## 모델 관련 ###########################
# netG 관련
Z_DIM = 100     # laten vector의 크기
G_HIDDEN = 64

# netD 관련 
D_HIDDEN = 64

################### 훈련 관련 ###########################
LR = 2e-4         # learning rate    
BATCH_SIZE = 128  # Adjust this value according to your GPU memory
EPOCH_NUM = 5

################### 기타 ################################
REAL_LABEL = 1.0
FAKE_LABEL = 0.0
SEED = 1     # Change to None to get different results at each run   

CUDA version: 11.3

cuda:0


# 시스템 초기화

In [16]:
print("PyTorch version: {}".format(torch.__version__))

#################### OUT_PATH 폴더 지우기 ####################
import shutil
def clear_folder(OUT_PATH):
    if os.path.exists(OUT_PATH) == True:
        shutil.rmtree('./output')

    os.mkdir('./output')
    
clear_folder(OUT_PATH)
print("Logging to {}\n".format(LOG_FILE))
#sys.stdout = utils.StdOut(LOG_FILE)

#################### SEED 관련 ##############################
if SEED is None:
    SEED = np.random.randint(1, 10000)
print("Random Seed: ", SEED)

np.random.seed(SEED)
torch.manual_seed(SEED)

if DEVICE == 'cuda:0':
    torch.cuda.manual_seed(SEED)
    
cudnn.benchmark = True      # May train faster but cost more memory

PyTorch version: 1.10.0
Logging to ./output\log.txt

Random Seed:  1


# 훈련데이터에 대한 데이터셋 및 데이터로더 제작
- 현재 버전은 download=True로 되어 있어 자동 로드 함
- 하지만, 해당 MNIST 사이트(http://yann.lecun.com/exdb/mnist/)가 유지보수 등으로 접속이 가능하지 않으면, 아래와 같이 직접 로드함
  - 사이트 : http://220.149.15.109:5960/sharing/lkzClL2Ix) 
  - 위 사이트를 클릭하여 MNIST.zip를 다운
  - 홈디렉토리(본 주피터 실행파일이 위치하고 있는 디렉토리)에 풀어 놓음

In [17]:
#################### 훈련 데이터셋 제작 ##############################
dataset = datasets.MNIST(root=DATA_PATH, download=True,   # train의 디폴트 값이 True 이며, 따라서
                     transform=transforms.Compose([        # MNIST/raw/train-images-idx3-ubyte에 대해 데이트셋 제작
                     transforms.Resize(X_DIM),
                     transforms.ToTensor(),
                     transforms.Normalize((0.5,), (0.5,))
                     ]))


# dataset = dset.ImageFolder(root=DATA_PATH,
#                            transform=transforms.Compose([
#                            transforms.Resize(X_DIM),
#                            transforms.CenterCrop(X_DIM),
#                            transforms.ToTensor(),
#                            transforms.Normalize((0.5, 0.5, 0.5), (0.5, 0.5, 0.5)),
#                            ]))

# dataset = dset.LSUN(root=DATA_PATH, classes=['bedroom_train'],
#                     transform=transforms.Compose([
#                     transforms.Resize(X_DIM),
#                     transforms.CenterCrop(X_DIM),
#                     transforms.ToTensor(),
#                     transforms.Normalize((0.5, 0.5, 0.5), (0.5, 0.5, 0.5)),
#                     ]))
#freeze_support()

assert dataset
torch.multiprocessing.freeze_support()

############## 훈련 데이터셋에 대한 대이터로더 제작 #######################
dataloader = torch.utils.data.DataLoader(dataset, batch_size=BATCH_SIZE, shuffle=True, 
                                         num_workers=WORKERS)

# worker를 1개롤 한 경우
#dataloader = torch.utils.data.DataLoader(dataset, batch_size=BATCH_SIZE, shuffle=True)

# Genertor와 Discriminator 생성

## G와 D의 가중치 초기화 함수

In [18]:
def weights_init(m):
    """custom weights initialization
    """
    classname = m.__class__.__name__
    if classname.find('Conv') != -1:
        m.weight.data.normal_(0.0, 0.02)
    elif classname.find('BatchNorm') != -1:
        m.weight.data.normal_(1.0, 0.02)
        m.bias.data.fill_(0)

## Generator

In [19]:
class Generator(nn.Module):
    def __init__(self):
        super(Generator, self).__init__()
        self.net = nn.Sequential(
            # 1st layer
            nn.ConvTranspose2d(Z_DIM, G_HIDDEN * 8, 4, 1, 0, bias=False), 
            nn.BatchNorm2d(G_HIDDEN * 8), nn.ReLU(True),
            # 2nd layer
            nn.ConvTranspose2d(G_HIDDEN * 8, G_HIDDEN * 4, 4, 2, 1, bias=False), 
            nn.BatchNorm2d(G_HIDDEN * 4),nn.ReLU(True),
            # 3rd layer
            nn.ConvTranspose2d(G_HIDDEN * 4, G_HIDDEN * 2, 4, 2, 1, bias=False),
            nn.BatchNorm2d(G_HIDDEN * 2), nn.ReLU(True),
            # 4th layer
            nn.ConvTranspose2d(G_HIDDEN * 2, G_HIDDEN, 4, 2, 1, bias=False), 
            nn.BatchNorm2d(G_HIDDEN), nn.ReLU(True),
            # output layer
            nn.ConvTranspose2d(G_HIDDEN, IMAGE_CHANNEL, 4, 2, 1, bias=False), nn.Tanh()
        )

    def forward(self, input):
        return self.net(input)

In [20]:
# 생성자 제작
netG = Generator().to(DEVICE)
netG.apply(weights_init)
print(netG)

Generator(
  (net): Sequential(
    (0): ConvTranspose2d(100, 512, kernel_size=(4, 4), stride=(1, 1), bias=False)
    (1): BatchNorm2d(512, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (2): ReLU(inplace=True)
    (3): ConvTranspose2d(512, 256, kernel_size=(4, 4), stride=(2, 2), padding=(1, 1), bias=False)
    (4): BatchNorm2d(256, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (5): ReLU(inplace=True)
    (6): ConvTranspose2d(256, 128, kernel_size=(4, 4), stride=(2, 2), padding=(1, 1), bias=False)
    (7): BatchNorm2d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (8): ReLU(inplace=True)
    (9): ConvTranspose2d(128, 64, kernel_size=(4, 4), stride=(2, 2), padding=(1, 1), bias=False)
    (10): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (11): ReLU(inplace=True)
    (12): ConvTranspose2d(64, 1, kernel_size=(4, 4), stride=(2, 2), padding=(1, 1), bias=False)
    (13): Tanh()
  )
)


## Discriminator

In [21]:
class Discriminator(nn.Module):
    def __init__(self):
        super(Discriminator, self).__init__()
        self.net = nn.Sequential(
            # 1st layer
            nn.Conv2d(IMAGE_CHANNEL, D_HIDDEN, 4, 2, 1, bias=False), nn.LeakyReLU(0.2, inplace=True),
            # 2nd layer
            nn.Conv2d(D_HIDDEN, D_HIDDEN * 2, 4, 2, 1, bias=False), 
            nn.BatchNorm2d(D_HIDDEN * 2), nn.LeakyReLU(0.2, inplace=True),
            # 3rd layer
            nn.Conv2d(D_HIDDEN * 2, D_HIDDEN * 4, 4, 2, 1, bias=False), 
            nn.BatchNorm2d(D_HIDDEN * 4), nn.LeakyReLU(0.2, inplace=True),
            # 4th layer
            nn.Conv2d(D_HIDDEN * 4, D_HIDDEN * 8, 4, 2, 1, bias=False), 
            nn.BatchNorm2d(D_HIDDEN * 8), nn.LeakyReLU(0.2, inplace=True),
            # output layer
            nn.Conv2d(D_HIDDEN * 8, 1, 4, 1, 0, bias=False), 
            nn.Sigmoid()
        )
    def forward(self, input):
        return self.net(input).view(-1, 1).squeeze(1)

In [22]:
# 판별자 생성
netD = Discriminator().to(DEVICE)
netD.apply(weights_init)
print(netD)

Discriminator(
  (net): Sequential(
    (0): Conv2d(1, 64, kernel_size=(4, 4), stride=(2, 2), padding=(1, 1), bias=False)
    (1): LeakyReLU(negative_slope=0.2, inplace=True)
    (2): Conv2d(64, 128, kernel_size=(4, 4), stride=(2, 2), padding=(1, 1), bias=False)
    (3): BatchNorm2d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (4): LeakyReLU(negative_slope=0.2, inplace=True)
    (5): Conv2d(128, 256, kernel_size=(4, 4), stride=(2, 2), padding=(1, 1), bias=False)
    (6): BatchNorm2d(256, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (7): LeakyReLU(negative_slope=0.2, inplace=True)
    (8): Conv2d(256, 512, kernel_size=(4, 4), stride=(2, 2), padding=(1, 1), bias=False)
    (9): BatchNorm2d(512, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (10): LeakyReLU(negative_slope=0.2, inplace=True)
    (11): Conv2d(512, 1, kernel_size=(4, 4), stride=(1, 1), bias=False)
    (12): Sigmoid()
  )
)


# 손실함수 및 옵티마이저 설정

In [23]:
criterion = nn.BCELoss()

optimizerD = optim.Adam(netD.parameters(), lr=LR, betas=(0.5, 0.999))
optimizerG = optim.Adam(netG.parameters(), lr=LR, betas=(0.5, 0.999))

# 훈련(Training)

In [24]:
from time import time
start_time = time()
viz_noise = torch.randn(BATCH_SIZE, Z_DIM, 1, 1, device=DEVICE) # G 테스트용 latent vector

for epoch in range(EPOCH_NUM):
    for i, data in enumerate(dataloader):
        x_real = data[0].to(DEVICE)
        
        real_label = torch.full((x_real.size(0),), REAL_LABEL, device=DEVICE)  
        fake_label = torch.full((x_real.size(0),), FAKE_LABEL, device=DEVICE)

        ################## netD 훈련 #####################
        # Train D with real data
        netD.zero_grad()
        y_real = netD(x_real)
        loss_D_real = criterion(y_real, real_label)
        loss_D_real.backward()

        # Train D with fake data
        z_noise = torch.randn(x_real.size(0), Z_DIM, 1, 1, device=DEVICE)
        x_fake = netG(z_noise)
        y_fake = netD(x_fake.detach())
        loss_D_fake = criterion(y_fake, fake_label)
        loss_D_fake.backward()
        optimizerD.step()

        ################## netG 훈련 #####################
        # Train G with fake data
        netG.zero_grad()
        y_fake_r = netD(x_fake)
        loss_G = criterion(y_fake_r, real_label)
        loss_G.backward()
        optimizerG.step()
        
        ################## 로깅:100번째 배치 마다 #####
        if i % 100 == 0:
            print('Epoch {} [{:4d}/{}] loss_D_real: {:.4f} loss_D_fake: {:.4f} loss_G: {:.4f}'.format(
                epoch, i, len(dataloader),
                loss_D_real.mean().item(),
                loss_D_fake.mean().item(),
                loss_G.mean().item()
            ))
            #vutils.save_image(x_real, os.path.join(OUT_PATH, 'real_samples.png'), normalize=True)
            
            with torch.no_grad():
                viz_sample = netG(viz_noise)
                vutils.save_image(viz_sample, os.path.join(OUT_PATH, 'gen_samples_{}_{}.png'.format(epoch, int(i/100))), 
                                                           normalize=True)
                
################## 에포크별 모델 저장 #####################                   
torch.save(netG.state_dict(), os.path.join(OUT_PATH, 'netG_{}.pth'.format(EPOCH_NUM)))
torch.save(netD.state_dict(), os.path.join(OUT_PATH, 'netD_{}.pth'.format(EPOCH_NUM)))

print(f"Traning ended : elapsed time {time()-start_time}")


Epoch 0 [   0/469] loss_D_real: 0.7730 loss_D_fake: 0.9116 loss_G: 3.9434
Epoch 0 [ 100/469] loss_D_real: 0.0260 loss_D_fake: 0.0099 loss_G: 7.3723
Epoch 0 [ 200/469] loss_D_real: 0.0021 loss_D_fake: 0.0032 loss_G: 7.5278
Epoch 0 [ 300/469] loss_D_real: 0.0012 loss_D_fake: 0.0019 loss_G: 7.2502
Epoch 0 [ 400/469] loss_D_real: 0.0035 loss_D_fake: 0.0035 loss_G: 7.6627
Epoch 1 [   0/469] loss_D_real: 0.1035 loss_D_fake: 0.0236 loss_G: 5.1195
Epoch 1 [ 100/469] loss_D_real: 0.0246 loss_D_fake: 0.1266 loss_G: 7.2055
Epoch 1 [ 200/469] loss_D_real: 0.0727 loss_D_fake: 0.2038 loss_G: 4.7624
Epoch 1 [ 300/469] loss_D_real: 0.4361 loss_D_fake: 0.0335 loss_G: 1.1360
Epoch 1 [ 400/469] loss_D_real: 0.0558 loss_D_fake: 0.0384 loss_G: 3.6747
Epoch 2 [   0/469] loss_D_real: 0.2800 loss_D_fake: 0.0745 loss_G: 2.3012
Epoch 2 [ 100/469] loss_D_real: 0.0402 loss_D_fake: 0.0763 loss_G: 3.6538
Epoch 2 [ 200/469] loss_D_real: 0.0472 loss_D_fake: 0.2492 loss_G: 3.2481
Epoch 2 [ 300/469] loss_D_real: 0.4426